In [30]:
import os
import sys
import glob
import json
import requests
import pandas as pd
from pathlib import Path
from google.cloud import bigquery
from IPython.core.debugger import set_trace
from tqdm.auto import tqdm
tqdm.pandas()

from tokenizer import MergedTokenizer

ImportError: cannot import name 'EntityRuler' from 'spacy.pipeline' (C:\ProgramData\Anaconda3\lib\site-packages\spacy\pipeline.cp37-win_amd64.pyd)

In [4]:
tagged_news = pd.read_pickle('tagged_news.pkl')

In [25]:
fnames = glob.glob('newsdata/downloaded/*.json')

In [26]:
fnames_to_tag = []
tagged_news_url = list(tagged_news.url)

for fname in tqdm(fnames[:1000]):
    js = json.loads(Path(fname).read_text())
    if js['url'] not in tagged_news_url:
        fnames_to_tag.append(fname)

In [29]:
texts = [json.loads(Path(fname).read_text())['text'] for fname in fnames_to_tag[:500]]; texts

['Stocks have been grinding sideways, but once they breakout, the move to the upside could be powerful, technical analysts say.\n\nThe S&P 500 has been edging closer to 3,028, its high from July 26, but it has backed off a number of times, creating a jagged seesaw pattern on August\'s chart. On Monday, the S&P was slightly higher but still trading below the psychological 3,000 level.\n\n"The intermediate and long term gauges that we track have relatively new buy signals. They are very widespread," said Katie Stockton founder and chief technical strategist at Fairlead Strategies. "Even in Japan, we\'re seeing signs of life from a momentum perspective. There\'s potential for it to be broad-based, not limited to the U.S."\n\nBut the stock market has not made much upside progress and the S&P 500 is only up 2.2% in the past 12 months, despite a December selloff and a recovery that began in January. There has also been tension between stocks and bonds, which have been reflecting fear of a we

In [44]:
texts = [json.loads(Path(f).read_text())['text'] for f in files[:489]]; texts

['(CNN) President Donald Trump said Wednesday that the US Food and Drug Administration would be putting out "some very strong recommendations" regarding the use of flavored e-cigarettes in "a couple of weeks."\n\nHealth and Human Services Secretary Alex Azar, seated in the Oval Office with the President, first lady Melania Trump and the acting commissioner of the FDA, announced that newly proposed enforcement policy would require flavored e-cigarette companies to take their products off the market.\n\n"It\'ll take several weeks for us to put out the final guidance that will announce all the parameters around the enforcement policy, and then there will likely be about a 30-day delay to effective date, as is customary," Azar said. But "at that point all flavored e-cigarettes other than tobacco flavor would have to be removed from the market."\n\nBy May 20, he said, e-cigarette companies making tobacco-flavored products would have the chance to file for approval by the FDA. At that time, 

In [45]:
headers = {"Authorization":"Token YbEhDr9hAYmd"}
endpoint = 'https://api.uclassify.com/v1/uclassify/IAB Taxonomy v2/classify'
data = json.dumps({'texts': texts})

response = requests.post(endpoint, headers=headers, data=data)

In [67]:
records = []
updated_at = str(pd.Timestamp.utcnow().date())

for i, resp in enumerate(tqdm(response.json())):
    cl = max(resp['classification'], key=lambda candidate:candidate['p'])
    file = json.loads(Path(files[i]).read_text())
    
    records.append({
        'url': file['url'], 
        'text': file['text'], 
        'uclass': cl['className'].split('_')[0], 
        'prob': cl['p'], 
        'updated_at': updated_at, 
    })
    
df = pd.DataFrame(records); df

prob                                               text  \
0    1.000000  (CNN) President Donald Trump said Wednesday th...   
1    0.431820  This momentous discovery was the beginning of ...   
2    0.393213  Let's not beat around the bush: the simple ans...   
3    0.454027  Maybe it was a coincidence. Maybe Dwayne Haski...   
4    0.759199  It’s hard to fault either the intention or the...   
5    0.310759  The indices have enjoyed a couple days of posi...   
6    0.401388  “Doing nothing about America’s gun violence cr...   
7    0.985436  JaVale McGee is reportedly the latest celebrit...   
8    1.000000  Xero has bolstered its machine learning capabi...   
9    1.000000  NEW DELHI (Reuters) - India banned the sale of...   
10   0.999997  "Take out the papers and the trash ..."\n\nIde...   
11   0.891335  New Orleans Saints quarterback Drew Brees has ...   
12   0.483917  The controversy over President Trump’s mysteri...   
13   0.406248  Brazil's federal data processing service Serpr...   
14   0.564089  More than 125 migrant mothers and children hav...   
15   0.669055  Gold futures moved lower on Friday, giving up ...   
16   0.531056  Written by Stella Ko, CNN Macao\n\nMany of Asi...   
17   0.411364  Rep. Mark Meadows said he is surprised by the ...   
18   0.522245  There are more Subway locations in America tha...   
19   0.316061  My partner and I have been very much in love f...   
20   0.679792  The Office of the Director of National Intelli...   
21   0.487312  The country's largest and best known gun right...   
22   0.681723  A man was found dead of trauma wounds in a fie...   
23   0.995411  XLNX stock was hit hard on Friday following ne...   
24   0.983101  ATLANTA — For decades, Atlanta Mayor Keisha La...   
25   0.999993  Add “startles easily” and “nervous smiler” nex...   
26   0.907265  Signs that read “Negro Mountain” have been rem...   
27   0.978547  While this looks mostly like a cynical ploy to...   
28   0.456622  Jurgen Klopp has insisted that his agent was j...   
29   0.438718  A New York judge has been forced to permanentl...   
..        ...                                                ...   
459  0.685041  (CNN) — A jungle-covered area on the east of B...   
460  0.986648  Purdue Pharma LP has secured support from 23 s...   
461  1.000000  Even if you diligently avoid caffeine late in ...   
462  0.999111  The inversion game makes me vomit. It's like w...   
463  0.996590  WASHINGTON (Reuters) - The White House on Sund...   
464  0.999737  It is 24 hours since Boris Johnson described h...   
465  0.999706  As tensions between Tehran and Washington reac...   
466  0.919980  British Prime Minister Boris Johnson has eclip...   
467  0.999913  WASHINGTON (Reuters) - Nearly two dozen U.S. l...   
468  0.943122  Antonio Brown’s corporate sponsors appear to b...   
469  0.999999  Saudi Aramco is likely to give roles to Citi, ...   
470  0.308976  Aaron Cresswell’s sublime free-kick helped dow...   
471  0.872217  An advertisement for animal rights organisatio...   
472  0.999217  SINGAPORE (Reuters) - Sebastian Vettel led Fer...   
473  0.765359  In the opening season of The Deuce, Emily Mead...   
474  0.330849  It's Friday 🎉 We made it. Here's how you can h...   
475  0.717260  I was going to pass by in silent contempt the ...   
476  0.446799  MONZA, Italy (Reuters) - Sebastian Vettel was ...   
477  0.648081  Graeme Gibson, the Canadian author, conservati...   
478  0.981319  WASHINGTON/ADDIS ABABA (Reuters) - Relatives o...   
479  0.777576  It is becoming increasingly clear that Raheem ...   
480  0.970125  The world's largest video game retailer, GameS...   
481  0.970403  What if they just starred in The Producers tho...   
482  0.963221  [TAIPEI] JPMorgan Chase & Co, which is in the ...   
483  0.788041  Jack Evans (D-Ward 2) speaks during a meeting ...   
484  0.483924  Welcome to POLITICO’s new cannabis newsletter!...   
485  0.982616  EPA Administrator Andrew Wheeler. | Zach Gibso... 

In [70]:
df.uclass.unique()

array(['healthy living', 'medical health', 'personal finance',
       'music and audio', 'pop culture', 'business and finance',
       'news and politics', 'automotive', 'education', 'sports',
       'family and relationships', 'television', 'movies', 'science',
       'events and attractions', 'technology and computing',
       'food and drink', 'books and literature', 'video gaming', 'travel',
       'fine art', 'careers', 'style and fashion', 'home and garden',
       'hobbies and interests', 'shopping', 'religion and spirituality',
       'pets'], dtype=object)

In [71]:
df.to_pickle('tagged_news.pkl')

In [72]:
pd.read_pickle('tagged_news.pkl')

prob                                               text  \
0    1.000000  (CNN) President Donald Trump said Wednesday th...   
1    0.431820  This momentous discovery was the beginning of ...   
2    0.393213  Let's not beat around the bush: the simple ans...   
3    0.454027  Maybe it was a coincidence. Maybe Dwayne Haski...   
4    0.759199  It’s hard to fault either the intention or the...   
5    0.310759  The indices have enjoyed a couple days of posi...   
6    0.401388  “Doing nothing about America’s gun violence cr...   
7    0.985436  JaVale McGee is reportedly the latest celebrit...   
8    1.000000  Xero has bolstered its machine learning capabi...   
9    1.000000  NEW DELHI (Reuters) - India banned the sale of...   
10   0.999997  "Take out the papers and the trash ..."\n\nIde...   
11   0.891335  New Orleans Saints quarterback Drew Brees has ...   
12   0.483917  The controversy over President Trump’s mysteri...   
13   0.406248  Brazil's federal data processing service Serpr...   
14   0.564089  More than 125 migrant mothers and children hav...   
15   0.669055  Gold futures moved lower on Friday, giving up ...   
16   0.531056  Written by Stella Ko, CNN Macao\n\nMany of Asi...   
17   0.411364  Rep. Mark Meadows said he is surprised by the ...   
18   0.522245  There are more Subway locations in America tha...   
19   0.316061  My partner and I have been very much in love f...   
20   0.679792  The Office of the Director of National Intelli...   
21   0.487312  The country's largest and best known gun right...   
22   0.681723  A man was found dead of trauma wounds in a fie...   
23   0.995411  XLNX stock was hit hard on Friday following ne...   
24   0.983101  ATLANTA — For decades, Atlanta Mayor Keisha La...   
25   0.999993  Add “startles easily” and “nervous smiler” nex...   
26   0.907265  Signs that read “Negro Mountain” have been rem...   
27   0.978547  While this looks mostly like a cynical ploy to...   
28   0.456622  Jurgen Klopp has insisted that his agent was j...   
29   0.438718  A New York judge has been forced to permanentl...   
..        ...                                                ...   
459  0.685041  (CNN) — A jungle-covered area on the east of B...   
460  0.986648  Purdue Pharma LP has secured support from 23 s...   
461  1.000000  Even if you diligently avoid caffeine late in ...   
462  0.999111  The inversion game makes me vomit. It's like w...   
463  0.996590  WASHINGTON (Reuters) - The White House on Sund...   
464  0.999737  It is 24 hours since Boris Johnson described h...   
465  0.999706  As tensions between Tehran and Washington reac...   
466  0.919980  British Prime Minister Boris Johnson has eclip...   
467  0.999913  WASHINGTON (Reuters) - Nearly two dozen U.S. l...   
468  0.943122  Antonio Brown’s corporate sponsors appear to b...   
469  0.999999  Saudi Aramco is likely to give roles to Citi, ...   
470  0.308976  Aaron Cresswell’s sublime free-kick helped dow...   
471  0.872217  An advertisement for animal rights organisatio...   
472  0.999217  SINGAPORE (Reuters) - Sebastian Vettel led Fer...   
473  0.765359  In the opening season of The Deuce, Emily Mead...   
474  0.330849  It's Friday 🎉 We made it. Here's how you can h...   
475  0.717260  I was going to pass by in silent contempt the ...   
476  0.446799  MONZA, Italy (Reuters) - Sebastian Vettel was ...   
477  0.648081  Graeme Gibson, the Canadian author, conservati...   
478  0.981319  WASHINGTON/ADDIS ABABA (Reuters) - Relatives o...   
479  0.777576  It is becoming increasingly clear that Raheem ...   
480  0.970125  The world's largest video game retailer, GameS...   
481  0.970403  What if they just starred in The Producers tho...   
482  0.963221  [TAIPEI] JPMorgan Chase & Co, which is in the ...   
483  0.788041  Jack Evans (D-Ward 2) speaks during a meeting ...   
484  0.483924  Welcome to POLITICO’s new cannabis newsletter!...   
485  0.982616  EPA Administrator Andrew Wheeler. | Zach Gibso... 